# Check change in mean slope
- Check the effect of changes in prestorm and poststorm mean slope.
- If there is a large berm, the prestorm mean slope (between dune toe and MHW) could be too small, and underpredict wave runup and TWL.


## Setup notebook

In [ ]:
# Enable autoreloading of our modules. 
# Most of the code will be located in the /src/ folder, 
# and then called from the notebook.
%matplotlib inline
%reload_ext autoreload
%autoreload

In [ ]:
from IPython.core.debugger import set_trace

import pandas as pd
import numpy as np
import os

import plotly
import plotly.graph_objs as go
import plotly.plotly as py
import plotly.tools as tools
import plotly.figure_factory as ff
import plotly.io as pio

import itertools

import matplotlib
from matplotlib import cm
import colorlover as cl

from ipywidgets import widgets, Output
from IPython.display import display, clear_output, Image, HTML

from sklearn.metrics import confusion_matrix

## Import data
Import our data into pandas Dataframes for the analysis. Data files are `.csv` files which are stored in the `./data/interim/` folder.

In [ ]:
def df_from_csv(csv, index_col, data_folder='../data/interim'):
    print('Importing {}'.format(csv))
    return pd.read_csv(os.path.join(data_folder,csv), index_col=index_col)

df_waves = df_from_csv('waves.csv', index_col=[0, 1])
df_tides = df_from_csv('tides.csv', index_col=[0, 1])
df_profiles = df_from_csv('profiles.csv', index_col=[0, 1, 2])
df_sites = df_from_csv('sites.csv', index_col=[0])
df_profile_features_crest_toes = df_from_csv('profile_features_crest_toes.csv', index_col=[0,1])

# Note that the forecasted data sets should be in the same order for impacts and twls
impacts = {
    'forecasted': {
        'foreshore_slope_sto06': df_from_csv('impacts_forecasted_foreshore_slope_sto06.csv', index_col=[0]),
        'mean_slope_sto06': df_from_csv('impacts_forecasted_mean_slope_sto06.csv', index_col=[0]),
        },
    'observed': df_from_csv('impacts_observed.csv', index_col=[0])
    }


twls = {
    'forecasted': {
        'foreshore_slope_sto06': df_from_csv('twl_foreshore_slope_sto06.csv', index_col=[0, 1]),
        'mean_slope_sto06':df_from_csv('twl_mean_slope_sto06.csv', index_col=[0, 1]),
    }
}
print('Done!')

# Plot prestorm vs poststorm mean slopes
Prestorm slopes have already been calculated as part of the TWL forecasting, however we'll need to extract the poststorm mean slopes from our profiles at each site.

In [ ]:
# Prestorm slopes are easy as we have already calculated this as part of the 
df_slopes_prestorm = twls['forecasted']['mean_slope_sto06'].groupby('site_id').head(1).reset_index().set_index(['site_id']).beta.to_frame()

# Get x and z at mhw (z=0.7m) for each site
z_mhw = 0.7
mhw_poststorm = []
for site, df in df_profiles.xs('poststorm', level='profile_type').groupby('site_id'):
    df = df.dropna(subset=['z'])
    df = df.iloc[(df['z']-z_mhw).abs().argsort().head(1)].reset_index()
    df = df.iloc[0]
    mhw_poststorm.append({
        'site_id': df.site_id,
        'x_mhw': df.x,
        'z_mhw': df.z
    })
#     break
df_mhw_poststorm = pd.DataFrame(mhw_poststorm)
df_mhw_poststorm = df_mhw_poststorm.set_index('site_id')

# Get x and z at poststorm dune toe for each site
df_dune_toe_poststorm = df_profile_features_crest_toes.xs('poststorm', level='profile_type')[['dune_toe_x','dune_toe_z']]

# Join df for mhw and dune toe
df = df_mhw_poststorm.join(df_dune_toe_poststorm)
df['beta'] = -(df['dune_toe_z'] - df['z_mhw']) / (df['dune_toe_x'] -df['x_mhw'])
df_slopes_poststorm = df['beta'].to_frame()

# Count how many nans
print('Number of nans: {}'.format(df_slopes_poststorm.beta.isna().sum()))

# Display dataframe
print('df_slopes_poststorm:')
df_slopes_poststorm

Now, let's join our post storm slopes, prestorm slopes, observed and forecasted impacts into one data frame to make it easier to plot.

In [ ]:
dfs = [df_slopes_poststorm.rename(columns={'beta':'poststorm_beta'}),
    df_slopes_prestorm.rename(columns={'beta':'prestorm_beta'}),
    impacts['observed']['storm_regime'].to_frame().rename(columns={'storm_regime': 'observed_regime'}),
    impacts['forecasted']['mean_slope_sto06']['storm_regime'].to_frame().rename(columns={'storm_regime': 'forecasted_regime'})
      ]

df = pd.concat(dfs, axis='columns')
df

In [ ]:
df_data.index

Plot our data

In [ ]:
fig = tools.make_subplots(
    rows=2,
    cols=2,
    specs=[[{}, {}], [{}, {}]],
    subplot_titles=('Swash/Swash',  'Swash/Collision', 
                    'Collision/Swash', 'Collision/Collision'),
 shared_xaxes=True, shared_yaxes=True,)


# Loop through combinations of observed/forecasted swash/collision
data = []
for forecasted_regime, observed_regime in itertools.product(['swash','collision'],repeat=2):
    
    # Get data for this combination 
    query = 'forecasted_regime=="{}" & observed_regime=="{}"'.format(forecasted_regime, observed_regime)
    df_data = df.query(query)
    print(query)
                  
    
    # Determine which subplot to plot results in
    if forecasted_regime == 'swash' and observed_regime == 'swash':
        x_col = 1
        y_col = 1
    elif forecasted_regime == 'collision' and observed_regime == 'collision':
        x_col = 2
        y_col = 2
    elif forecasted_regime == 'swash' and observed_regime == 'collision':
        x_col = 2
        y_col = 1
    elif forecasted_regime == 'collision' and observed_regime == 'swash':
        x_col = 1
        y_col = 2
    else:
        print('something went wrong')
        continue

    fig.append_trace(
        go.Scatter(
            x=df_data.prestorm_beta,
            y=df_data.poststorm_beta,
            text = df_data.index.tolist(),
            hoverinfo = 'text',
            mode = 'markers',
            line = dict(
        color = ('rgba(22, 22, 22, 0.2)'),
        width = 0.5,)),
            x_col,
            y_col)

# layout = go.Layout(
#     xaxis=dict(domain=[0, 0.45]),
#     yaxis=dict(
#         domain=[0, 0.45],
#         type='log',
#     ),
#     xaxis2=dict(domain=[0.55, 1]),
#     xaxis4=dict(domain=[0.55, 1], anchor='y4'),
#     yaxis3=dict(
#         domain=[0.55, 1],
#         type='log',
#     ),
#     yaxis4=dict(
#         domain=[0.55, 1],
#         anchor='x4',
#         type='log',
#     ))

fig['layout'].update(showlegend=False, title='Specs with Subplot Title',height=800,)

for ax in ['yaxis','yaxis2']:
#     fig['layout'][ax]['type']='log'
    fig['layout'][ax]['range']= [0,0.2]

for ax in ['xaxis', 'xaxis2']:
    fig['layout'][ax]['range']= [0,0.2]

go.FigureWidget(fig)

Looking at the above plot:
- In general, we can see that the prestorm mean slope is flatter than the poststorm mean slope. This can be explained by the presence of prestorm berms, which increase the prestorm mean slope. During the storm, these berms get eroded and decrease the slope.
- **Collision/Collision**: Where we observe and predict collision, we see steeper prestorm slopes. This is to be expected since larger slopes will generate more runup and higher TWLs.
- **Swash/Collision**: Where we predict collision but observe swash, we can see that the prestorm mean slopes >0.1 generate high TWLs. 

